In [1]:
#%pip install torch==2.5.1 torchvision==0.20.1 torchaudio==2.5.1 --index-url https://download.pytorch.org/whl/cu124 --force-reinstall

In [2]:
import torch

def format_pytorch_version(version_str):
    # Example input: "2.0.1+cu118" -> returns "2.0.1"
    return version_str.split('+')[0]

def format_cuda_version(cuda_str):
    # If CUDA is None (CPU-only PyTorch), return "cpu"
    if cuda_str is None:
        return "cpu"
    # Example: "11.8" -> "cu118"
    return "cu" + cuda_str.replace('.', '')

TORCH_version = torch.__version__
TORCH = format_pytorch_version(TORCH_version)
CUDA_version = torch.version.cuda
CUDA = format_cuda_version(CUDA_version)

print(f"Installing packages for torch-{TORCH}+{CUDA}...")

%pip install --upgrade --no-cache-dir pyg_lib torch_scatter torch_sparse torch_cluster torch_spline_conv -f https://data.pyg.org/whl/torch-{TORCH}+{CUDA}.html

%pip install torch_geometric

Installing packages for torch-2.5.1+cu124...
Looking in links: https://data.pyg.org/whl/torch-2.5.1+cu124.html
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [3]:
%pip install scikit-learn imbalanced-learn xgboost

Note: you may need to restart the kernel to use updated packages.


In [4]:
%pip install optuna

Note: you may need to restart the kernel to use updated packages.


### Hyperparameter Optimization Citeseer
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 3, 27),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.03, 0.28),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv', 'TransformerConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [128,256,512,1024,2048]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "reliable_mini_batch":True,
        "seeds": 5,
        "output_csv": "citeseer_scar_sampling.csv"
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-03 17:17:34,794] A new study created in memory with name: no-name-c23aa730-a525-4ad2-933b-93852d087458


Running experiment with seed=654:
 - alpha=0.5, K=21, layers=1, hidden=128, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.10898462659764199, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=SAGEConv, rate_pairs=7, batch_size=512
Epoch 0, Loss: 2.7945
 - Metrics: Accuracy=0.9312, F1=0.8248, Recall=0.7689, Precision=0.8894
Running experiment with seed=114:
 - alpha=0.5, K=21, layers=1, hidden=128, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.10898462659764199, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=SAGEConv, rate_pairs=7, batch_size=512
Epoch 0, Loss: 2.7120
 - Metrics: Accuracy=0.9321, F1=0.8280, Recall=0.7760, Precision=0.8874
Running experiment with seed=25:
 - alpha=0.5, K=21, layers=1, hidden=128, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.10898462659764199, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=SAGEConv, rate_pairs=7, batch_size=512
Epoch 0, Los

[I 2025-03-03 17:18:15,695] Trial 0 finished with value: 0.8273627895222889 and parameters: {'K': 21, 'layers': 1, 'hidden_channels': 128, 'out_channels': 64, 'ratio': 0.10898462659764199, 'aggregation': 'sum', 'treatment': 'removal', 'model_type': 'SAGEConv', 'rate_pairs': 7, 'batch_size': 512, 'lr': 0.005516011281102024}. Best is trial 0 with value: 0.8273627895222889.


 - Metrics: Accuracy=0.9321, F1=0.8280, Recall=0.7760, Precision=0.8874
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_0303171734.csv.
Average F1 over valid seeds: 0.8274 ± 0.0013
Running experiment with seed=654:
 - alpha=0.5, K=14, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2695543181158462, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=GCNConv, rate_pairs=6, batch_size=512
Epoch 0, Loss: 2.3823
 - Metrics: Accuracy=0.9339, F1=0.8497, Recall=0.8873, Precision=0.8152
Running experiment with seed=114:
 - alpha=0.5, K=14, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2695543181158462, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=GCNConv, rate_pairs=6, batch_size=512
Epoch 0, Loss: 2.3333
 - Metrics: Accuracy=0.9309, F1=0.8433, Recall=0.8830, Precision=0.8070
Running experiment with seed=25:
 - alpha=0.5, K=14, layers=1, hidden=2

[I 2025-03-03 17:19:07,420] Trial 1 finished with value: 0.8461177441772676 and parameters: {'K': 14, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.2695543181158462, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GCNConv', 'rate_pairs': 6, 'batch_size': 512, 'lr': 0.0017914955582350109}. Best is trial 1 with value: 0.8461177441772676.


...

 - Metrics: Accuracy=0.9435, F1=0.8661, Recall=0.8673, Precision=0.8649
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_0303184009.csv.
Average F1 over valid seeds: 0.8633 ± 0.0020
Running experiment with seed=654:
 - alpha=0.5, K=12, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.1749273789903748, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=GATConv, rate_pairs=8, batch_size=512
Epoch 0, Loss: 2.2123
 - Metrics: Accuracy=0.9333, F1=0.8351, Recall=0.8017, Precision=0.8713
Running experiment with seed=114:
 - alpha=0.5, K=12, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.1749273789903748, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=GATConv, rate_pairs=8, batch_size=512
Epoch 0, Loss: 2.1738
 - Metrics: Accuracy=0.9339, F1=0.8392, Recall=0.8188, Precision=0.8606
Running experiment with seed=25:
 - alpha=0.5, K=12, layers=2, hidden=1

[I 2025-03-03 18:42:02,873] Trial 98 finished with value: 0.8357110411709394 and parameters: {'K': 12, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.1749273789903748, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GATConv', 'rate_pairs': 8, 'batch_size': 512, 'lr': 0.0005957431748959286}. Best is trial 73 with value: 0.8705614592709011.


 - Metrics: Accuracy=0.9321, F1=0.8336, Recall=0.8074, Precision=0.8615
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_0303184110.csv.
Average F1 over valid seeds: 0.8357 ± 0.0021
Running experiment with seed=654:
 - alpha=0.5, K=24, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.1805071002891241, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=GATConv, rate_pairs=6, batch_size=512
Epoch 0, Loss: 2.7558
 - Metrics: Accuracy=0.9432, F1=0.8651, Recall=0.8645, Precision=0.8657
Running experiment with seed=114:
 - alpha=0.5, K=24, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.1805071002891241, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=GATConv, rate_pairs=6, batch_size=512
Epoch 0, Loss: 2.6524
 - Metrics: Accuracy=0.9420, F1=0.8636, Recall=0.8716, Precision=0.8557
Running experiment with seed=25:
 - alpha=0.5, K=24, layers=1, hidden=1

[I 2025-03-03 18:42:59,875] Trial 99 finished with value: 0.8646601418856935 and parameters: {'K': 24, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.1805071002891241, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GATConv', 'rate_pairs': 6, 'batch_size': 512, 'lr': 0.0056653566172875916}. Best is trial 73 with value: 0.8705614592709011.


 - Metrics: Accuracy=0.9447, F1=0.8691, Recall=0.8716, Precision=0.8667
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_0303184202.csv.
Average F1 over valid seeds: 0.8647 ± 0.0027
Best trial:
  Average F1: 0.8705614592709011
  Best parameters:
    K: 24
    layers: 1
    hidden_channels: 256
    out_channels: 256
    ratio: 0.16900728321877106
    aggregation: mean
    treatment: removal
    model_type: GATConv
    rate_pairs: 7
    batch_size: 256
    lr: 0.0003010383072180728


In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 3, 27),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.09, 0.25),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [128,256,512,1024,2048]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "reliable_mini_batch":True,
        "seeds": 5,
        "output_csv": "citeseer_scar_sampling_nnif_batch_cluster.csv",
        "min":0.82
    }
    
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-05 14:43:35,741] A new study created in memory with name: no-name-7fe166a7-9ecf-4536-b740-e1860661e14d


Running experiment with seed=654:
 - alpha=0.5, K=15, layers=2, hidden=64, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.22860138741901403, pos_weight=1, aggregation=sum, treatment=relabeling
 - model_type=GCNConv, rate_pairs=9, batch_size=512, reliable_mini_batch=True


Computing METIS partitioning...
Done!


Epoch 0, Loss: 2.6603
Epoch 10, Loss: 2.3651
Epoch 20, Loss: 2.1426
Epoch 30, Loss: 2.2074
Epoch 40, Loss: 2.1687
Epoch 50, Loss: 2.2312
Epoch 60, Loss: 2.0390
Epoch 70, Loss: 2.0979
Epoch 80, Loss: 1.9901
Epoch 90, Loss: 2.0019


[I 2025-03-05 14:45:16,616] Trial 0 finished with value: 0.6390328151986183 and parameters: {'K': 15, 'layers': 2, 'hidden_channels': 64, 'out_channels': 64, 'ratio': 0.22860138741901403, 'aggregation': 'sum', 'treatment': 'relabeling', 'model_type': 'GCNConv', 'rate_pairs': 9, 'batch_size': 512, 'lr': 0.00547461638120661}. Best is trial 0 with value: 0.6390328151986183.


 - Metrics: Accuracy=0.8115, F1=0.6390, Recall=0.7917, Precision=0.5357
F1 = 0.64 < 0.82, skipping ...
Done. Results written to citeseer_experimentations\citeseer_scar_sampling_nnif_batch_cluster_0503144335.csv.
Average F1 over valid seeds: 0.6390 ± 0.0000
Running experiment with seed=654:
 - alpha=0.5, K=6, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.19536871497782118, pos_weight=1, aggregation=mean, treatment=removal
 - model_type=SAGEConv, rate_pairs=7, batch_size=2048, reliable_mini_batch=True


Computing METIS partitioning...
Done!


Epoch 0, Loss: 0.5665
Epoch 10, Loss: 0.4596
Epoch 20, Loss: 0.4582
Epoch 30, Loss: 0.4569
Epoch 40, Loss: 0.4556
Epoch 50, Loss: 0.4543
Epoch 60, Loss: 0.4529


### Hyperparameter Optimization Citeseer
#### SAR 

In [6]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 13, 27),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.08, 0.28),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv', 'TransformerConv']),
        "sampling_mode":trial.suggest_categorical("sampling_mode", [None,'nn', 'random', 'feature']), #'weighted',
        "num_neighbors": trial.suggest_int("num_neighbors", 5, 20),
        "seeds": 5,
        "output_csv": "citeseer_sar_conv_sampling.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-28 06:14:09,568] A new study created in memory with name: no-name-42bbce78-54ef-4c58-b6b4-681334e6d510


Running experiment with seed=1:
 - alpha=0.5, K=19, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2344547193646393, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6555, LPL: 1.2741, Contrastive: 0.0369
 - Metrics: Accuracy=0.9396, F1=0.8525, Recall=0.8288, Precision=0.8776
Running experiment with seed=2:
 - alpha=0.5, K=19, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2344547193646393, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6328, LPL: 1.2233, Contrastive: 0.0422
 - Metrics: Accuracy=0.9369, F1=0.8478, Recall=0.8345, Precision=0.8616
Running experiment with seed=3:
 - alpha=0.5, K=19, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2344547193646393, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6751, LPL: 1.3092, Contrastive: 0.0410
 - Metrics: Accuracy=0.9393, F1=0.8545, Recall=0.

[I 2025-02-28 06:15:07,063] Trial 0 finished with value: 0.8459918694509939 and parameters: {'K': 19, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.2344547193646393, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GATConv', 'sampling_mode': None, 'num_neighbors': 7}. Best is trial 0 with value: 0.8459918694509939.


 - Metrics: Accuracy=0.9387, F1=0.8532, Recall=0.8459, Precision=0.8607
Done. Results written to citeseer_experimentations\citeseer_sar_conv_sampling_2802061409.csv.
Average F1 over valid seeds: 0.8460 ± 0.0123
Running experiment with seed=1:
 - alpha=0.5, K=23, layers=2, hidden=128, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.21101856458586588, pos_weight=1, aggregation=mean, treatment=relabeling
Epoch 0, Loss: 0.6707, LPL: 1.2602, Contrastive: 0.0812
Epoch 50, Loss: 0.6301, LPL: 1.2602, Contrastive: 0.0000
Epoch 100, Loss: 10.3286, LPL: 20.6569, Contrastive: 0.0004


[I 2025-02-28 06:15:32,343] Trial 1 finished with value: 0.0 and parameters: {'K': 23, 'layers': 2, 'hidden_channels': 128, 'out_channels': 128, 'ratio': 0.21101856458586588, 'aggregation': 'mean', 'treatment': 'relabeling', 'model_type': 'SAGEConv', 'sampling_mode': 'feature', 'num_neighbors': 11}. Best is trial 0 with value: 0.8459918694509939.


...

 - Metrics: Accuracy=0.9402, F1=0.8434, Recall=0.7646, Precision=0.9404
Done. Results written to citeseer_experimentations\citeseer_sar_conv_sampling_2802191438.csv.
Average F1 over valid seeds: 0.8366 ± 0.0077
Running experiment with seed=1:
 - alpha=0.5, K=23, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.14963015662719242, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.7889, LPL: 1.4040, Contrastive: 0.1739
Epoch 50, Loss: 0.7021, LPL: 1.4040, Contrastive: 0.0001
Epoch 100, Loss: 10.3429, LPL: 20.6858, Contrastive: 0.0000
 - Metrics: Accuracy=0.9423, F1=0.8590, Recall=0.8345, Precision=0.8850
Running experiment with seed=2:
 - alpha=0.5, K=23, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.14963015662719242, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.7414, LPL: 1.3002, Contrastive: 0.1826
Epoch 50, Loss: 0.6502, LPL: 1.3002, Contrastive: 0.0002
Epo

[I 2025-02-28 19:17:36,154] Trial 498 finished with value: 0.8636526089357872 and parameters: {'K': 23, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.14963015662719242, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GATConv', 'sampling_mode': 'random', 'num_neighbors': 18}. Best is trial 257 with value: 0.8664629413441904.


 - Metrics: Accuracy=0.9450, F1=0.8657, Recall=0.8417, Precision=0.8912
Done. Results written to citeseer_experimentations\citeseer_sar_conv_sampling_2802191604.csv.
Average F1 over valid seeds: 0.8637 ± 0.0026
Running experiment with seed=1:
 - alpha=0.5, K=23, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.15484523321908383, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.7854, LPL: 1.4009, Contrastive: 0.1698
Epoch 50, Loss: 0.7005, LPL: 1.4009, Contrastive: 0.0001
Epoch 100, Loss: 10.3418, LPL: 20.6837, Contrastive: 0.0000
 - Metrics: Accuracy=0.9393, F1=0.8519, Recall=0.8288, Precision=0.8763
Running experiment with seed=2:
 - alpha=0.5, K=23, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.15484523321908383, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.7378, LPL: 1.2968, Contrastive: 0.1788
Epoch 50, Loss: 0.6485, LPL: 1.2968, Contrastive: 0.0002
Epo

[I 2025-02-28 19:18:57,825] Trial 499 finished with value: 0.8605505313805768 and parameters: {'K': 23, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.15484523321908383, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GATConv', 'sampling_mode': None, 'num_neighbors': 14}. Best is trial 257 with value: 0.8664629413441904.


 - Metrics: Accuracy=0.9426, F1=0.8601, Recall=0.8374, Precision=0.8840
Done. Results written to citeseer_experimentations\citeseer_sar_conv_sampling_2802191736.csv.
Average F1 over valid seeds: 0.8606 ± 0.0053
Best trial:
  Average F1: 0.8664629413441904
  Best parameters:
    K: 23
    layers: 1
    hidden_channels: 128
    out_channels: 256
    ratio: 0.13406788588633956
    aggregation: mean
    treatment: removal
    model_type: GATConv
    sampling_mode: random
    num_neighbors: 14


### Hyperparameter Optimization Cora
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "cora",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 3, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.14, 0.36),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [128,256,512,1024,2048]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "reliable_mini_batch":True,
        "seeds": 5,
        "output_csv": "cora_scar_sampling_nnif_batch_cluster.csv",
        "min":0.84
    }

    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-05 14:40:17,700] A new study created in memory with name: no-name-ca884db3-732b-4a75-a874-69c10620a33c


Running experiment with seed=654:
 - alpha=0.5, K=31, layers=2, hidden=64, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2776942245218562, pos_weight=1, aggregation=sum, treatment=relabeling
 - model_type=GINConv, rate_pairs=9, batch_size=512, reliable_mini_batch=True


Computing METIS partitioning...
Done!


Epoch 0, Loss: 4.4633
Epoch 10, Loss: 4.1918
Epoch 20, Loss: 4.2851


[I 2025-03-05 14:41:00,316] Trial 0 finished with value: 0.712372790573112 and parameters: {'K': 31, 'layers': 2, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.2776942245218562, 'aggregation': 'sum', 'treatment': 'relabeling', 'model_type': 'GINConv', 'rate_pairs': 9, 'batch_size': 512, 'lr': 0.0027129883241093855}. Best is trial 0 with value: 0.712372790573112.


 - Metrics: Accuracy=0.8017, F1=0.7124, Recall=0.8130, Precision=0.6339
F1 = 0.71 < 0.84, skipping ...
Done. Results written to cora_experimentations\cora_scar_sampling_nnif_batch_cluster_0503144017.csv.
Average F1 over valid seeds: 0.7124 ± 0.0000
Running experiment with seed=654:
 - alpha=0.5, K=20, layers=1, hidden=64, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.08361208516534752, pos_weight=1, aggregation=sum, treatment=relabeling
 - model_type=GATConv, rate_pairs=2, batch_size=2048, reliable_mini_batch=True


Computing METIS partitioning...
Done!


Epoch 0, Loss: 0.8147
Epoch 10, Loss: 0.4359
Epoch 20, Loss: 0.4204
Epoch 30, Loss: 0.4181
Epoch 40, Loss: 0.4170
Epoch 50, Loss: 0.4161
Epoch 60, Loss: 0.4153


[W 2025-03-05 14:41:48,464] Trial 1 failed with parameters: {'K': 20, 'layers': 1, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.08361208516534752, 'aggregation': 'sum', 'treatment': 'relabeling', 'model_type': 'GATConv', 'rate_pairs': 2, 'batch_size': 2048, 'lr': 0.007278166225138826} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "c:\Users\romai\Desktop\gnn\gnn_pu\.conda\Lib\site-packages\optuna\study\_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
                      ^^^^^^^^^^^
  File "C:\Users\romai\AppData\Local\Temp\ipykernel_2064812\2066334259.py", line 40, in objective
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
                     ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\romai\Desktop\gnn\gnn_pu\NNIF-GNN\train_NNIF_GNN.py", line 562, in run_nnif_gnn_experiment
    model, train_losses = main(data, train_params, device)
                          ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

KeyboardInterrupt: 

### Hyperparameter Optimization Cora
#### SAR 

In [8]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "cora",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 23, 38),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.08, 0.48),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv', 'TransformerConv']),
        "sampling_mode":trial.suggest_categorical("sampling_mode", [None,'nn', 'random', 'feature']), #'weighted',
        "num_neighbors": trial.suggest_int("num_neighbors", 5, 20),
        "seeds": 5,
        "output_csv": "cora_sar_conv_sampling.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-01 16:53:35,815] A new study created in memory with name: no-name-e1f8e2d5-ff39-4b89-9e59-8646eef7518b


Running experiment with seed=1:
 - alpha=0.5, K=26, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.25255002650187486, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.5976, LPL: 1.1784, Contrastive: 0.0167
Epoch 50, Loss: 0.5892, LPL: 1.1784, Contrastive: 0.0000
 - Metrics: Accuracy=0.9273, F1=0.8805, Recall=0.8875, Precision=0.8736
Running experiment with seed=2:
 - alpha=0.5, K=26, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.25255002650187486, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.6435, LPL: 1.2683, Contrastive: 0.0187
Epoch 50, Loss: 0.6342, LPL: 1.2683, Contrastive: 0.0000
Epoch 100, Loss: 11.2190, LPL: 22.4379, Contrastive: 0.0001
 - Metrics: Accuracy=0.9287, F1=0.8820, Recall=0.8814, Precision=0.8825
Running experiment with seed=3:
 - alpha=0.5, K=26, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0

[I 2025-03-01 16:54:34,121] Trial 0 finished with value: 0.8726218242518842 and parameters: {'K': 26, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.25255002650187486, 'aggregation': 'sum', 'treatment': 'removal', 'model_type': 'SAGEConv', 'sampling_mode': None, 'num_neighbors': 5}. Best is trial 0 with value: 0.8726218242518842.


 - Metrics: Accuracy=0.9228, F1=0.8742, Recall=0.8875, Precision=0.8612
Done. Results written to cora_experimentations\cora_sar_conv_sampling_0103165335.csv.
Average F1 over valid seeds: 0.8726 ± 0.0082
Running experiment with seed=1:
 - alpha=0.5, K=34, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.4505857723008272, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6981, LPL: 1.3725, Contrastive: 0.0237
Epoch 50, Loss: 0.6863, LPL: 1.3725, Contrastive: 0.0000
Epoch 100, Loss: 13.6773, LPL: 27.3545, Contrastive: 0.0000
 - Metrics: Accuracy=0.8896, F1=0.8343, Recall=0.9205, Precision=0.7629
Running experiment with seed=2:
 - alpha=0.5, K=34, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.4505857723008272, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.7376, LPL: 1.4580, Contrastive: 0.0173
Epoch 50, Loss: 0.7290, LPL: 1.4580, Contrastive: 0.0000
 - Metrics: A

[I 2025-03-01 16:55:54,309] Trial 1 finished with value: 0.8298003251944014 and parameters: {'K': 34, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.4505857723008272, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GCNConv', 'sampling_mode': 'random', 'num_neighbors': 17}. Best is trial 0 with value: 0.8726218242518842.


...

 - Metrics: Accuracy=0.9391, F1=0.8942, Recall=0.8521, Precision=0.9406
Done. Results written to cora_experimentations\cora_sar_conv_sampling_0203080037.csv.
Average F1 over valid seeds: 0.8924 ± 0.0067
Running experiment with seed=1:
 - alpha=0.5, K=33, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.19174030449629417, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6603, LPL: 1.2367, Contrastive: 0.0839
Epoch 50, Loss: 0.6184, LPL: 1.2367, Contrastive: 0.0001
 - Metrics: Accuracy=0.9324, F1=0.8816, Recall=0.8325, Precision=0.9367
Running experiment with seed=2:
 - alpha=0.5, K=33, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.19174030449629417, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6970, LPL: 1.3245, Contrastive: 0.0695
Epoch 50, Loss: 0.6623, LPL: 1.3245, Contrastive: 0.0001
Epoch 100, Loss: 13.6119, LPL: 27.2236, Contrastive: 0.0001
 - Metrics:

[I 2025-03-02 08:03:50,847] Trial 498 finished with value: 0.8937810684228097 and parameters: {'K': 33, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.19174030449629417, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GCNConv', 'sampling_mode': 'random', 'num_neighbors': 16}. Best is trial 494 with value: 0.8976928061087911.


 - Metrics: Accuracy=0.9413, F1=0.8966, Recall=0.8423, Precision=0.9583
Done. Results written to cora_experimentations\cora_sar_conv_sampling_0203080227.csv.
Average F1 over valid seeds: 0.8938 ± 0.0097
Running experiment with seed=1:
 - alpha=0.5, K=32, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.19509247262405416, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6450, LPL: 1.2217, Contrastive: 0.0683
Epoch 50, Loss: 0.6109, LPL: 1.2217, Contrastive: 0.0001
Epoch 100, Loss: 13.4486, LPL: 26.8972, Contrastive: 0.0001
 - Metrics: Accuracy=0.9361, F1=0.8899, Recall=0.8545, Precision=0.9283
Running experiment with seed=2:
 - alpha=0.5, K=32, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.19509247262405416, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.6870, LPL: 1.3159, Contrastive: 0.0581
Epoch 50, Loss: 0.6580, LPL: 1.3159, Contrastive: 0.0001
Epoch 100, 

[I 2025-03-02 08:05:46,475] Trial 499 finished with value: 0.8948114189030061 and parameters: {'K': 32, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.19509247262405416, 'aggregation': 'mean', 'treatment': 'removal', 'model_type': 'GCNConv', 'sampling_mode': 'feature', 'num_neighbors': 16}. Best is trial 494 with value: 0.8976928061087911.


 - Metrics: Accuracy=0.9420, F1=0.9003, Recall=0.8667, Precision=0.9366
Done. Results written to cora_experimentations\cora_sar_conv_sampling_0203080350.csv.
Average F1 over valid seeds: 0.8948 ± 0.0042
Best trial:
  Average F1: 0.8976928061087911
  Best parameters:
    K: 33
    layers: 2
    hidden_channels: 256
    out_channels: 256
    ratio: 0.1931276009868142
    aggregation: mean
    treatment: removal
    model_type: GCNConv
    sampling_mode: feature
    num_neighbors: 16


### Hyperparameter Optimization Pubmed
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "pubmed",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 3, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.2, 0.4),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [512,1024,2048,5096,10192]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "reliable_mini_batch":True,
        "seeds": 5,
        "output_csv": "pubmed_scar_sampling_nnif_batch_cluster.csv",
        "min": 0.82
        }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-03-04 09:36:49,109] A new study created in memory with name: no-name-f6306d18-b471-4ee4-b69b-b8b1d1c9223c


Running experiment with seed=654:
 - alpha=0.5, K=13, layers=1, hidden=64, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.20433911888475717, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=SAGEConv, rate_pairs=1, batch_size=2048, reliable_mini_batch=True
Epoch 0, Loss: 0.8487
 - Metrics: Accuracy=0.8772, F1=0.8325, Recall=0.7638, Precision=0.9147
Running experiment with seed=114:
 - alpha=0.5, K=13, layers=1, hidden=64, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.20433911888475717, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=SAGEConv, rate_pairs=1, batch_size=2048, reliable_mini_batch=True
Epoch 0, Loss: 0.8568
 - Metrics: Accuracy=0.8771, F1=0.8322, Recall=0.7634, Precision=0.9147
Running experiment with seed=25:
 - alpha=0.5, K=13, layers=1, hidden=64, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.20433911888475717, pos_weight=1, aggregation=sum, treatment=removal
 - model_ty

[I 2025-03-04 09:57:37,520] Trial 0 finished with value: 0.8327658401155029 and parameters: {'K': 13, 'layers': 1, 'hidden_channels': 64, 'out_channels': 256, 'ratio': 0.20433911888475717, 'aggregation': 'sum', 'treatment': 'removal', 'model_type': 'SAGEConv', 'rate_pairs': 1, 'batch_size': 2048, 'lr': 0.008870480387387797}. Best is trial 0 with value: 0.8327658401155029.


 - Metrics: Accuracy=0.8775, F1=0.8329, Recall=0.7643, Precision=0.9150
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_0403093649.csv.
Average F1 over valid seeds: 0.8328 ± 0.0004
Running experiment with seed=654:
 - alpha=0.5, K=17, layers=1, hidden=128, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.23916397215432553, pos_weight=1, aggregation=mean, treatment=relabeling
 - model_type=SAGEConv, rate_pairs=1, batch_size=5096, reliable_mini_batch=True
Epoch 0, Loss: 0.4637


[I 2025-03-04 10:00:51,730] Trial 1 finished with value: 0.7365728900255755 and parameters: {'K': 17, 'layers': 1, 'hidden_channels': 128, 'out_channels': 64, 'ratio': 0.23916397215432553, 'aggregation': 'mean', 'treatment': 'relabeling', 'model_type': 'SAGEConv', 'rate_pairs': 1, 'batch_size': 5096, 'lr': 0.005697155733849093}. Best is trial 0 with value: 0.8327658401155029.


...

 - Metrics: Accuracy=0.8947, F1=0.8635, Recall=0.8338, Precision=0.8954
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_0503122746.csv.
Average F1 over valid seeds: 0.8644 ± 0.0006
Running experiment with seed=654:
 - alpha=0.5, K=28, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2859526722183263, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=GCNConv, rate_pairs=9, batch_size=10192, reliable_mini_batch=True
Epoch 0, Loss: 0.7398
 - Metrics: Accuracy=0.8938, F1=0.8654, Recall=0.8543, Precision=0.8767
Running experiment with seed=114:
 - alpha=0.5, K=28, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2859526722183263, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=GCNConv, rate_pairs=9, batch_size=10192, reliable_mini_batch=True
Epoch 0, Loss: 0.7475
 - Metrics: Accuracy=0.8950, F1=0.8669, Recall=0.8561, Precision=0.8780
Running ex

[I 2025-03-05 13:13:44,886] Trial 85 finished with value: 0.8666848701039431 and parameters: {'K': 28, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.2859526722183263, 'aggregation': 'sum', 'treatment': 'removal', 'model_type': 'GCNConv', 'rate_pairs': 9, 'batch_size': 10192, 'lr': 0.001773752829794359}. Best is trial 85 with value: 0.8666848701039431.


 - Metrics: Accuracy=0.8948, F1=0.8666, Recall=0.8554, Precision=0.8781
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_0503125100.csv.
Average F1 over valid seeds: 0.8667 ± 0.0007
Running experiment with seed=654:
 - alpha=0.5, K=28, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2701901463472635, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=GCNConv, rate_pairs=9, batch_size=10192, reliable_mini_batch=True
Epoch 0, Loss: 0.7389
 - Metrics: Accuracy=0.8956, F1=0.8660, Recall=0.8447, Precision=0.8885
Running experiment with seed=114:
 - alpha=0.5, K=28, layers=2, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2701901463472635, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=GCNConv, rate_pairs=9, batch_size=10192, reliable_mini_batch=True
Epoch 0, Loss: 0.7476
 - Metrics: Accuracy=0.8969, F1=0.8679, Recall=0.8481, Precision=0.8886
Running ex

[I 2025-03-05 13:36:10,845] Trial 86 finished with value: 0.8669204295207769 and parameters: {'K': 28, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'ratio': 0.2701901463472635, 'aggregation': 'sum', 'treatment': 'removal', 'model_type': 'GCNConv', 'rate_pairs': 9, 'batch_size': 10192, 'lr': 0.0017008485459745135}. Best is trial 86 with value: 0.8669204295207769.


 - Metrics: Accuracy=0.8954, F1=0.8661, Recall=0.8465, Precision=0.8866
Done. Results written to pubmed_experimentations\pubmed_scar_sampling_nnif_batch_0503131344.csv.
Average F1 over valid seeds: 0.8669 ± 0.0008
Running experiment with seed=654:
 - alpha=0.5, K=31, layers=2, hidden=128, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2880635276942003, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=GCNConv, rate_pairs=9, batch_size=10192, reliable_mini_batch=True
Epoch 0, Loss: 0.7573
 - Metrics: Accuracy=0.8918, F1=0.8628, Recall=0.8514, Precision=0.8744
Running experiment with seed=114:
 - alpha=0.5, K=31, layers=2, hidden=128, out=64
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.2880635276942003, pos_weight=1, aggregation=sum, treatment=removal
 - model_type=GCNConv, rate_pairs=9, batch_size=10192, reliable_mini_batch=True
Epoch 0, Loss: 0.7647
 - Metrics: Accuracy=0.8900, F1=0.8615, Recall=0.8564, Precision=0.8667
Running expe

### Hyperparameter Optimization Pubmed
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "pubmed",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 23, 38),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.08, 0.48),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv', 'TransformerConv']),
        "sampling_mode":trial.suggest_categorical("sampling_mode", [None,'nn', 'random', 'feature']), #'weighted',
        "num_neighbors": trial.suggest_int("num_neighbors", 5, 20),
        "seeds": 5,
        "output_csv": "pubmed_sar_conv_sampling.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-26 03:23:53,936] A new study created in memory with name: no-name-7f4cbf8f-985f-4bdf-acf7-67c58479d826


Running experiment with seed=1:
 - alpha=0.5, K=29, layers=2, hidden=128, out=128
 - norm=None, dropout=0.13019271568601654, margin=0.5, lpl_weight=0.9617526580395241
 - ratio=0.4686918535680597, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.5174, LPL: 1.5777, Contrastive: 0.0002
Epoch 50, Loss: 1.5174, LPL: 1.5777, Contrastive: 0.0001
 - Metrics: Accuracy=0.8649, F1=0.8455, Recall=0.9258, Precision=0.7780
Running experiment with seed=2:
 - alpha=0.5, K=29, layers=2, hidden=128, out=128
 - norm=None, dropout=0.13019271568601654, margin=0.5, lpl_weight=0.9617526580395241
 - ratio=0.4686918535680597, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.4896, LPL: 1.5488, Contrastive: 0.0002
Epoch 50, Loss: 1.4896, LPL: 1.5488, Contrastive: 0.0001
 - Metrics: Accuracy=0.8669, F1=0.8460, Recall=0.9154, Precision=0.7864
Running experiment with seed=3:
 - alpha=0.5, K=29, layers=2, hidden=128, out=128
 - norm=None, dropout=0.13019271568601654, margin=0.5, l

[I 2025-02-26 03:26:12,321] Trial 0 finished with value: 0.8441785629649907 and parameters: {'K': 29, 'layers': 2, 'hidden_channels': 128, 'out_channels': 128, 'dropout': 0.13019271568601654, 'lpl_weight': 0.9617526580395241, 'ratio': 0.4686918535680597, 'aggregation': 'mean'}. Best is trial 0 with value: 0.8441785629649907.


 - Metrics: Accuracy=0.8643, F1=0.8438, Recall=0.9177, Precision=0.7810
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602032353.csv.
Average F1 over 5 seeds: 0.8442 ± 0.0014
Running experiment with seed=1:
 - alpha=0.5, K=35, layers=1, hidden=256, out=128
 - norm=None, dropout=0.2998522859023272, margin=0.5, lpl_weight=0.5609886595645283
 - ratio=0.4704598795028684, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.9071, LPL: 1.6155, Contrastive: 0.0019
Epoch 50, Loss: 0.9064, LPL: 1.6155, Contrastive: 0.0001
Epoch 100, Loss: 14.6880, LPL: 26.1823, Contrastive: 0.0000
 - Metrics: Accuracy=0.8733, F1=0.8544, Recall=0.9305, Precision=0.7897
Running experiment with seed=2:
 - alpha=0.5, K=35, layers=1, hidden=256, out=128
 - norm=None, dropout=0.2998522859023272, margin=0.5, lpl_weight=0.5609886595645283
 - ratio=0.4704598795028684, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.8935, LPL: 1.5912, Contrastive: 0.0019
Epo

[I 2025-02-26 03:29:46,339] Trial 1 finished with value: 0.853918427311636 and parameters: {'K': 35, 'layers': 1, 'hidden_channels': 256, 'out_channels': 128, 'dropout': 0.2998522859023272, 'lpl_weight': 0.5609886595645283, 'ratio': 0.4704598795028684, 'aggregation': 'mean'}. Best is trial 1 with value: 0.853918427311636.


...

 - Metrics: Accuracy=0.9031, F1=0.8767, Recall=0.8629, Precision=0.8910
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602075820.csv.
Average F1 over 5 seeds: 0.8782 ± 0.0032
Running experiment with seed=1:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.13511458111879743, margin=0.5, lpl_weight=0.2231074780696927
 - ratio=0.2698667009750044, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.3213, LPL: 1.4392, Contrastive: 0.0003
Epoch 50, Loss: 0.3212, LPL: 1.4392, Contrastive: 0.0001
Epoch 100, Loss: 4.5760, LPL: 20.5103, Contrastive: 0.0000
 - Metrics: Accuracy=0.9000, F1=0.8747, Recall=0.8739, Precision=0.8755
Running experiment with seed=2:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.13511458111879743, margin=0.5, lpl_weight=0.2231074780696927
 - ratio=0.2698667009750044, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.3172, LPL: 1.4205, Contrastive: 0.0003
Ep

[I 2025-02-26 08:05:25,112] Trial 98 finished with value: 0.8754223410387084 and parameters: {'K': 25, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.13511458111879743, 'lpl_weight': 0.2231074780696927, 'ratio': 0.2698667009750044, 'aggregation': 'mean'}. Best is trial 83 with value: 0.8798047359394902.


 - Metrics: Accuracy=0.8978, F1=0.8722, Recall=0.8728, Precision=0.8715
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602080152.csv.
Average F1 over 5 seeds: 0.8754 ± 0.0036
Running experiment with seed=1:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.11095177279889956, margin=0.5, lpl_weight=0.3240380657010947
 - ratio=0.26709136300274616, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.4664, LPL: 1.4388, Contrastive: 0.0003
Epoch 50, Loss: 0.4663, LPL: 1.4388, Contrastive: 0.0001
Epoch 100, Loss: 6.6475, LPL: 20.5144, Contrastive: 0.0000
 - Metrics: Accuracy=0.9016, F1=0.8767, Recall=0.8757, Precision=0.8777
Running experiment with seed=2:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.11095177279889956, margin=0.5, lpl_weight=0.3240380657010947
 - ratio=0.26709136300274616, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.4593, LPL: 1.4168, Contrastive: 0.0003


[I 2025-02-26 08:08:59,181] Trial 99 finished with value: 0.8772450709674819 and parameters: {'K': 25, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.11095177279889956, 'lpl_weight': 0.3240380657010947, 'ratio': 0.26709136300274616, 'aggregation': 'mean'}. Best is trial 83 with value: 0.8798047359394902.


 - Metrics: Accuracy=0.9014, F1=0.8762, Recall=0.8738, Precision=0.8787
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602080525.csv.
Average F1 over 5 seeds: 0.8772 ± 0.0023
Best trial:
  Average F1: 0.8798047359394902
  Best parameters:
    K: 26
    layers: 2
    hidden_channels: 64
    out_channels: 64
    dropout: 0.1254611964387077
    lpl_weight: 0.24515372552362366
    ratio: 0.24282619680377082
    aggregation: mean


### Hyperparameter Optimization WikiCS
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "wiki-cs",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 3, 40),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.03, 0.38),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [512,1024,2048,5096,10192]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "reliable_mini_batch":True,
        "seeds": 5,
        "output_csv": "wikics_scar_sampling_nnif_batch_cluster.csv",
        "min": 0.85

        }

    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


### Hyperparameter Optimization WikiCS
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "wiki-cs",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 23, 48),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.08, 0.48),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv', 'TransformerConv']),
        "sampling_mode":trial.suggest_categorical("sampling_mode", [None,'nn', 'random', 'feature']), #'weighted',
        "num_neighbors": trial.suggest_int("num_neighbors", 5, 20),
        "seeds": 5,
        "output_csv": "wikics_sar_conv_sampling.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-27 00:23:43,749] A new study created in memory with name: no-name-0651131d-f94f-4263-836d-989f224364c3


Running experiment with seed=1:
 - alpha=0.5, K=40, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6561213398778427
 - ratio=0.1474974595079506, pos_weight=1, aggregation=sum, treatment=relabeling


ERROR:root:Anomaly detector error: ValueError('Input contains NaN.')


Epoch 0, Loss: nan, LPL: 19.9822, Contrastive: nan
 - Metrics: Accuracy=0.9242, F1=0.8401, Recall=0.8697, Precision=0.8124
Running experiment with seed=2:
 - alpha=0.5, K=40, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6561213398778427
 - ratio=0.1474974595079506, pos_weight=1, aggregation=sum, treatment=relabeling


ERROR:root:Anomaly detector error: ValueError('Input contains NaN.')


...

 - Metrics: Accuracy=0.9616, F1=0.9151, Recall=0.9037, Precision=0.9269
Done. Results written to wiki-cs_experimentations\wikics_sar_learnable_params_2702031150.csv.
Average F1 over 5 seeds: 0.9073 ± 0.0053
Running experiment with seed=1:
 - alpha=0.5, K=30, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6942151968028537
 - ratio=0.10619648424454017, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.0359, LPL: 2.9326, Contrastive: 0.0001
 - Metrics: Accuracy=0.9519, F1=0.8876, Recall=0.8302, Precision=0.9537
Running experiment with seed=2:
 - alpha=0.5, K=30, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6942151968028537
 - ratio=0.10619648424454017, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.0087, LPL: 2.8935, Contrastive: 0.0001
 - Metrics: Accuracy=0.9562, F1=0.8982, Recall=0.8429, Precision=0.9613
Running experiment with seed=3:
 - alpha=0.5, K=30, layers=1, hidden=256, out=2

[I 2025-02-27 03:15:41,895] Trial 98 finished with value: 0.8959296946004663 and parameters: {'K': 30, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.6942151968028537, 'ratio': 0.10619648424454017, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 93 with value: 0.9076936562210944.


 - Metrics: Accuracy=0.9575, F1=0.9015, Recall=0.8492, Precision=0.9607
Done. Results written to wiki-cs_experimentations\wikics_sar_learnable_params_2702031345.csv.
Average F1 over 5 seeds: 0.8959 ± 0.0046
Running experiment with seed=1:
 - alpha=0.5, K=29, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6520900081642776
 - ratio=0.1301604391586133, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.8344, LPL: 2.8131, Contrastive: 0.0001
 - Metrics: Accuracy=0.9561, F1=0.9006, Recall=0.8694, Precision=0.9342
Running experiment with seed=2:
 - alpha=0.5, K=29, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6520900081642776
 - ratio=0.1301604391586133, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.8131, LPL: 2.7804, Contrastive: 0.0001
 - Metrics: Accuracy=0.9596, F1=0.9089, Recall=0.8806, Precision=0.9391
Running experiment with seed=3:
 - alpha=0.5, K=29, layers=1, hidden=256, out=256

[I 2025-02-27 03:17:37,071] Trial 99 finished with value: 0.9078176666989897 and parameters: {'K': 29, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.6520900081642776, 'ratio': 0.1301604391586133, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 99 with value: 0.9078176666989897.


 - Metrics: Accuracy=0.9597, F1=0.9092, Recall=0.8802, Precision=0.9402
Done. Results written to wiki-cs_experimentations\wikics_sar_learnable_params_2702031541.csv.
Average F1 over 5 seeds: 0.9078 ± 0.0037
Best trial:
  Average F1: 0.9078176666989897
  Best parameters:
    K: 29
    layers: 1
    hidden_channels: 256
    out_channels: 256
    lpl_weight: 0.6520900081642776
    ratio: 0.1301604391586133
    aggregation: mean
    treatment: removal


# Elliptic Bitcoin

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "elliptic-bitcoin",      
        "mechanism": "SAR2",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 3, 40),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.03, 0.38),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv']),
        "rate_pairs":trial.suggest_int("rate_pairs",1,10),
        "batch_size": trial.suggest_categorical("batch_size", [2548,5096,10192,20384,40768]),
        "lr": trial.suggest_float("lr", 1e-4, 1e-2),
        "reliable_mini_batch":True,
        "seeds": 5,
        "output_csv": "elliptic_bitcoin_cluster.csv",
        "min":0.65
        }

    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")
